In [22]:
import numpy as np
import sys
data = np.load('out.npy') # out.npy should be written by test_get_ccif.py

num,nsize,xdeg=data.shape
print('data shape of out.npy=',data.shape)

rfac=3 # scale factor for the data
densitymap=False
isomin=2
isomax=10
mmm=20

#onlybatch1=True
#if(onlybatch1):
#    data=data[0:1,0:nsize,0:3] 
#else:
#    data=data.reshape(1,num*nsize,3)

#import time
#import matplotlib.pyplot as plt
#from mpl_toolkits.mplot3d import proj3d

#for i in range(1):
#    x = data[i,:,0]
#    y = data[i,:,1]
#    z = data[i,:,2]
#    fig = plt.figure(figsize=(8, 8))
#    ax = fig.add_subplot(111, projection='3d', proj_type='ortho')
#    #Plot with very small marker
#    ax.scatter(x, y, z, s=0.5)
#    #plt.show()

data=rfac*data
#print(data.shape)
#print(datax.shape)
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd

#print(data.shape)
idx=num
for id in range(0,idx): #idx,idx+1):
    ndat=data[id,:,:].shape[0]
    #print(ndat,data[id,:,:].shape[1])
    datax=np.zeros((ndat,4))
    distance=np.zeros((ndat))
    datax[0:ndat,0:3]=data[id,0:ndat,0:3]
    #break
    for ip in range(0,datax.shape[0]):
       dis=np.sum(np.array(data[id,ip,0:3])**2)**0.5
       
#############################
       #dis=0 if ip>2048 else 1
       #dis=2 if ip>4096 else dis
       #if(ip==0): dis=3resume
#############################       
       
       datax[ip,3]=dis
       #if(dis>3.3):datax[ip,3]=100
       distance[ip]=dis

    distance.sort()

    #sort datax by x
    #ix= np.argsort(datax, axis=0)
    #for i in range(ndat):
    #    print(datax[ix,:])
    
    #mask=(distance>0.1)
    #distance=distance[mask]
    old=0
    ncount=0
    for i in range(0,distance.shape[0]):
        ncount=ncount+1
        if(distance[i]>old+0.1):
          #print(old,ncount)
          old=distance[i]
          ncount=0


    if densitymap: # Create density map
        x = np.linspace(-mmm, mmm, 50)
        y = np.linspace(-mmm, mmm, 50)
        z = np.linspace(-mmm, mmm, 50)
        x, y, z = np.meshgrid(x, y, z)
        
        for i in range(0,ndat):
            xc=datax[i,0]
            yc=datax[i,1]
            zc=datax[i,2]
            rr=.3
            densityadd =np.exp(-(x-xc)**2/rr + -(y-yc)**2/rr + -(z-zc)**2/rr)
            if(i==0): 
                density = densityadd
            else:
                density = densityadd + density
        # Create a 3D surface plot
        fig = go.Figure(data=go.Volume(
            x=x.flatten(),
            y=y.flatten(),
            z=z.flatten(),
            value=density.flatten(),
            isomin=isomin,
            isomax=isomax,
            opacity=0.1,  # needs to be small to see through all surfaces
            surface_count=10,  # number of isosurfaces, 2 by default
        ))

        # Set plot title and axis labels
        fig.update_layout(
            title='Probablity map of atoms(we have an atom at the center)',
            scene=dict(
                xaxis_title='X',
                yaxis_title='Y',
                zaxis_title='Z'
            )
        )          

        fig.update_layout(width=800, height=800)
        fig.write_html("./zeolite_sampling_density."+str(id)+".html")
        #fig.show()
        #continue
    
    #print('id=',id,'len=',len(datax) ,datax.shape)
    # データフレームのデータを描画する
    df  = pd.DataFrame(datax,columns=['x','y','z','cc'])
    fig = px.scatter_3d(df, x='x', y='y', z='z', color='cc')
    # Set aspect ratio to be equal
    #projection orqtho
    fig.update_layout(scene=dict(camera=dict(projection=dict(type="orthographic"))))
    
    fig.update_layout(
    scene=dict(
        xaxis=dict(range=[-mmm, mmm]),
        yaxis=dict(range=[-mmm, mmm]),
        zaxis=dict(range=[-mmm, mmm]),
        aspectmode='cube'
    ))
    #プロットのサイズを変更
    #プロットのキャプションを変更
    #カラーバーのタイトルを変更
    fig.update_layout(coloraxis_colorbar=dict(title='Distance(Å)'))
    # fig.update_layout(title=\
    #     "Fig.1: A samping of {<B>r</B>} by p(<B>r</B>|<B>z</B>) for a 256-dimentional random latent vector <B>z</B>.<BR>\
    #     After we prepared Si-centerd 6192 clusters (within 6 Å, Si only) taken from Zeolite<BR>\
    #     database, we let Diffucion-Point-Cloud(DPC) learn <br>\
    #     the randomly-rotated clusters. <br>\
    #     The color represents the distance from the central Si.")
    fig.update_layout(width=800, height=800)
    fig.update_layout(scene_aspectmode='cube')
    #fig.update_traces(marker=dict(size=5))
    fig.update_traces(marker=dict(size=2))
    fig.write_html("./zeolite_sampling."+str(id)+".html")
    fig.show()


data shape of out.npy= (1, 512, 3)
[[[-27.26369476  -3.79400444  -5.52046919  28.07452774]
  [ -2.41373467 -18.05332947  -3.06162596  18.46949768]
  [ -0.51685202   3.00766706 -21.81475449  22.02718163]
  [  0.20942712   0.21298577   0.04634742   0.30227593]]

 [[-26.27892303   6.05913925 -11.46494102  29.30426407]
  [ -2.45062447 -18.04290009  -3.06096268  18.46405411]
  [ 12.18591213  -9.12332153 -20.64489746  25.65040398]
  [  0.21014924   0.21190804   0.05114977   0.30279371]]

 [[-23.22848129   2.22997236 -10.72848606  25.68337059]
  [  7.1000762  -15.70141125   0.27425244  17.23428726]
  [ -0.26916167  -0.65600723 -16.35486221  16.37022591]
  [  0.20988263   0.21878837   0.05043931   0.30734867]]

 ...

 [[ 17.73160934   4.07600021  20.82037544  27.64980698]
  [  1.53612161  18.7550106   -0.70558798  18.83103752]
  [  6.13900566   4.72754097  18.74433136  20.2826767 ]
  [-27.26369476  -3.79400444  -5.52046919  28.07452774]]

 [[ 17.87288284 -13.86307335   2.62745714  22.77121544]